**Data Science Capstone project**  
Course 9 project

**Imports**

In [1]:
!pip install folium

import pandas as pd
import numpy as np
import requests
import folium
from sklearn.cluster import KMeans
import matplotlib.cm as cm
import matplotlib.colors as colors

**Load and wrangle indexes data from Wikipedia**


In [2]:
# Load raw data from Wikipedia
df = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')[0]


# Remove NA Boroughs
is_not_na = df['Borough'] != 'Not assigned'
df1 = df[is_not_na]


# Treat NA Neighbourhoods
df2 = df1.copy()
for index, row in df2.iterrows():
    if df2.loc[index,'Neighbourhood'] == 'Not assigned':
       df2.loc[index,'Neighbourhood'] = df2.loc[index,'Borough']


# Note: Rows are already merged by Postal Code


**View DF shape**

In [3]:
df2.shape

(103, 3)

**Load coordinates data**

In [4]:
coordinates_df = pd.read_csv('https://cocl.us/Geospatial_data')
coordinates_df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

**Add Coordinates** 

In [5]:
df3 = pd.merge(left=df2, right=coordinates_df, left_on='Postal Code', right_on='Postal Code')
print(df3.shape)
df3.head()


(103, 5)


Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

In [6]:
CLIENT_ID = 'SBPPJXXVK3DNXUMMAEXGNQ5DRZDY5DAPBQB5RS3VDEVBIYAD' # your Foursquare ID
CLIENT_SECRET = '{hidden}' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value


In [7]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        #print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [8]:
venues = getNearbyVenues(names=df3['Neighbourhood'],
                                   latitudes=df3['Latitude'],
                                   longitudes=df3['Longitude'],
                                   radius=500
                                  )

In [9]:
print(venues.shape)
venues.head()

(2117, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3               Portugril       43.725819       -79.312785   
4             Tim Hortons       43.725517       -79.313103   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3  Portuguese Restaurant  
4            Coffee Shop

In [10]:
map1 = folium.Map(location=[df3.loc[0, 'Latitude'], df3.loc[0, 'Longitude']], zoom_start=11)

# add markers to map
for lat, lng, label in zip(venues['Venue Latitude'], venues['Venue Longitude'], venues['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map1)  
    
map1

### We see more rural Neighbourhoods have lower density, so it's hard to compare them to more central ones as we're using a single Radius parameter for all of them. Let's try to focus on the ones that have a 'Toronto' in their Boroughs for now.


In [11]:
df31 = df3[df3['Borough'].str.contains('Toronto')]
venues31 = getNearbyVenues(names=df31['Neighbourhood'],
                                   latitudes=df31['Latitude'],
                                   longitudes=df31['Longitude']
                                  )


In [12]:
map31 = folium.Map(location=[df31.loc[2, 'Latitude'], df31.loc[2, 'Longitude']], zoom_start=11)

# add markers to map
for lat, lng, label in zip(venues31['Venue Latitude'], venues31['Venue Longitude'], venues31['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map31)  
    
map31

In [13]:
# one hot encoding
toronto_onehot = pd.get_dummies(venues31[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = venues31['Neighborhood'] 

# move neighborhood column to the first column
nbh = toronto_onehot['Neighborhood']
toronto_onehot.drop(labels=['Neighborhood'], axis=1,inplace = True)
toronto_onehot.insert(0, 'Neighborhood', nbh)

toronto_onehot.head()

Neighborhood  Airport  Airport Food Court  Airport Lounge  \
0  Regent Park, Harbourfront        0                   0               0   
1  Regent Park, Harbourfront        0                   0               0   
2  Regent Park, Harbourfront        0                   0               0   
3  Regent Park, Harbourfront        0                   0               0   
4  Regent Park, Harbourfront        0                   0               0   

   Airport Service  Airport Terminal  American Restaurant  Antique Shop  \
0                0                 0                    0             0   
1                0                 0                    0             0   
2                0                 0                    0             0   
3                0                 0                    0             0   
4                0                 0                    0             0   

   Aquarium  Art Gallery  ...  Tibetan Restaurant  Toy / Game Store  Trail  \
0         0            0  ...                   0                 0      0   
1         0            0  ...                   0                 0      0   
2         0            0  ...                   0                 0      0   
3         0            0  ...                   0                 0      0   
4         0            0  ...                   0                 0      0   

   Train Station  Vegetarian / Vegan Restaurant  Video Game Store  \
0              0                              0                 0   
1              0                              0                 0   
2              0                              0                 0   
3              0                              0                 0   
4              0                              0                 0   

   Vietnamese Restaurant  Wine Bar  Wine Shop  Yoga Studio  
0                      0         0          0            0  
1                      0         0          0            0  
2                      0         0          0            0  
3                      0         0          0            0  
4                      0         0          0            0  

[5 rows x 234 columns]

In [14]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood   Airport  \
0                                         Berczy Park  0.000000   
1        Brockton, Parkdale Village, Exhibition Place  0.000000   
2   Business reply mail Processing Centre, South C...  0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...  0.066667   
4                                  Central Bay Street  0.000000   
5                                            Christie  0.000000   
6                                Church and Wellesley  0.000000   
7                      Commerce Court, Victoria Hotel  0.000000   
8                                          Davisville  0.000000   
9                                    Davisville North  0.000000   
10                       Dufferin, Dovercourt Village  0.000000   
11             First Canadian Place, Underground city  0.000000   
12    Forest Hill North & West, Forest Hill Road Park  0.000000   
13                           Garden District, Ryerson  0.000000   
14  Harbourfront East, Union Station, Toronto Islands  0.000000   
15                      High Park, The Junction South  0.000000   
16                     India Bazaar, The Beaches West  0.000000   
17          Kensington Market, Chinatown, Grange Park  0.000000   
18                                      Lawrence Park  0.000000   
19                           Little Portugal, Trinity  0.000000   
20                        Moore Park, Summerhill East  0.000000   
21                  North Toronto West, Lawrence Park  0.000000   
22                             Parkdale, Roncesvalles  0.000000   
23        Queen's Park, Ontario Provincial Government  0.000000   
24                          Regent Park, Harbourfront  0.000000   
25                           Richmond, Adelaide, King  0.000000   
26                                           Rosedale  0.000000   
27                                           Roselawn  0.000000   
28                                 Runnymede, Swansea  0.000000   
29                                     St. James Town  0.000000   
30                        St. James Town, Cabbagetown  0.000000   
31                                     Stn A PO Boxes  0.000000   
32                                    Studio District  0.000000   
33  Summerhill West, Rathnelly, South Hill, Forest...  0.000000   
34                The Annex, North Midtown, Yorkville  0.000000   
35                                        The Beaches  0.000000   
36                       The Danforth West, Riverdale  0.000000   
37           Toronto Dominion Centre, Design Exchange  0.000000   
38                     University of Toronto, Harbord  0.000000   

    Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0             0.000000        0.000000              0.0          0.000000   
1             0.000000        0.000000              0.0          0.000000   
2             0.000000        0.000000              0.0          0.000000   
3             0.066667        0.133333              0.2          0.133333   
4             0.000000        0.000000              0.0          0.000000   
5             0.000000        0.000000              0.0          0.000000   
6             0.000000        0.000000              0.0          0.000000   
7             0.000000        0.000000              0.0          0.000000   
8             0.000000        0.000000              0.0          0.000000   
9             0.000000        0.000000              0.0          0.000000   
10            0.000000        0.000000              0.0          0.000000   
11            0.000000        0.000000              0.0          0.000000   
12            0.000000        0.000000              0.0          0.000000   
13            0.000000        0.000000              0.0          0.000000   
14            0.000000        0.000000              0.0          0.000000   
15            0.000000        0.000000              0.0          0.000000   
16            0.000000        0.000000             

In [15]:
#

In [16]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [17]:
#
# Let's take only 7 as the density seems to be lower than in NY where value of 10 was used
#
num_top_venues = 7

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Berczy Park           Coffee Shop   
1       Brockton, Parkdale Village, Exhibition Place                  Café   
2  Business reply mail Processing Centre, South C...    Light Rail Station   
3  CN Tower, King and Spadina, Railway Lands, Har...       Airport Service   
4                                 Central Bay Street           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0          Cocktail Bar              Beer Bar           Cheese Shop   
1        Breakfast Spot             Nightclub           Coffee Shop   
2         Auto Workshop           Pizza Place            Comic Shop   
3        Airport Lounge      Airport Terminal               Airport   
4        Sandwich Place                  Café    Italian Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  
0                Bakery            Restaurant        Farmers Market  
1             Pet Store          Climbing Gym         Burrito Place  
2            Restaurant         Burrito Place               Brewery  
3              Boutique      Sculpture Garden                 Plane  
4          Burger Joint       Bubble Tea Shop           Salad Place

# Cluster Neighborhoods

In [18]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:20] 

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1],
      dtype=int32)

In [19]:
# add clustering labels
neighborhoods_venues_sorted_w_clusters = neighborhoods_venues_sorted.copy()
neighborhoods_venues_sorted_w_clusters.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df31.copy()
toronto_merged.rename(columns={"Neighbourhood": "Neighborhood"}, inplace=True)

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted_w_clusters.set_index('Neighborhood'), on='Neighborhood')


# Visualize

In [20]:
# create map
map_clusters = folium.Map(location=[df31.loc[2, 'Latitude'], df31.loc[2, 'Longitude']], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examine Clusters

In [21]:

toronto_merged.head(50)

Postal Code           Borough  \
2           M5A  Downtown Toronto   
4           M7A  Downtown Toronto   
9           M5B  Downtown Toronto   
15          M5C  Downtown Toronto   
19          M4E      East Toronto   
20          M5E  Downtown Toronto   
24          M5G  Downtown Toronto   
25          M6G  Downtown Toronto   
30          M5H  Downtown Toronto   
31          M6H      West Toronto   
36          M5J  Downtown Toronto   
37          M6J      West Toronto   
41          M4K      East Toronto   
42          M5K  Downtown Toronto   
43          M6K      West Toronto   
47          M4L      East Toronto   
48          M5L  Downtown Toronto   
54          M4M      East Toronto   
61          M4N   Central Toronto   
62          M5N   Central Toronto   
67          M4P   Central Toronto   
68          M5P   Central Toronto   
69          M6P      West Toronto   
73          M4R   Central Toronto   
74          M5R   Central Toronto   
75          M6R      West Toronto   
79          M4S   Central Toronto   
80          M5S  Downtown Toronto   
81          M6S      West Toronto   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
86          M4V   Central Toronto   
87          M5V  Downtown Toronto   
91          M4W  Downtown Toronto   
92          M5W  Downtown Toronto   
96          M4X  Downtown Toronto   
97          M5X  Downtown Toronto   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   

                                          Neighborhood   Latitude  Longitude  \
2                            Regent Park, Harbourfront  43.654260 -79.360636   
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494   
9                             Garden District, Ryerson  43.657162 -79.378937   
15                                      St. James Town  43.651494 -79.375418   
19                                         The Beaches  43.676357 -79.293031   
20                                         Berczy Park  43.644771 -79.373306   
24                                  Central Bay Street  43.657952 -79.387383   
25                                            Christie  43.669542 -79.422564   
30                            Richmond, Adelaide, King  43.650571 -79.384568   
31                        Dufferin, Dovercourt Village  43.669005 -79.442259   
36   Harbourfront East, Union Station, Toronto Islands  43.640816 -79.381752   
37                            Little Portugal, Trinity  43.647927 -79.419750   
41                        The Danforth West, Riverdale  43.679557 -79.352188   
42            Toronto Dominion Centre, Design Exchange  43.647177 -79.381576   
43        Brockton, Parkdale Village, Exhibition Place  43.636847 -79.428191   
47                      India Bazaar, The Beaches West  43.668999 -79.315572   
48                      Commerce Court, Victoria Hotel  43.648198 -79.379817   
54                                     Studio District  43.659526 -79.340923   
61                                       Lawrence Park  43.728020 -79.388790   
62                                            Roselawn  43.711695 -79.416936   
67                                    Davisville North  43.712751 -79.390197   
68     Forest Hill North & West, Forest Hill Road Park  43.696948 -79.411307   
69                       High Park, The Junction South  43.661608 -79.464763   
73                   North Toronto West, Lawrence Park  43.715383 -79.405678   
74                 The Annex, North Midtown, Yorkville  43.672710 -79.405678   
75                              Parkdale, Roncesvalles  43.648960 -79.456325   
79                                          Davisville  43.704324 -79.388790   
80                      University of Toronto, Harbord  43.662696 -79.400049   
81                                  Runnymede, Swansea  43.651571 -79.484450   
83                         Moore Park, Summerhill East  43.689574 -79.383160   
84           Kensington Market, Chinatown, 

# Results

Neighbourhoods are pretty similar in the central part of Toronto.
Most of them have a wide variaty of coffe shops, restaraunts and other entertainment-related places. Business ventures are also highly popular, but are not widely represented in an available data set.
